# Imports

In [1]:
%cd /../baselines/meta-transfer-learning/scripts

/../baselines/meta-transfer-learning/scripts


In [2]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import normalize
from rnn_models import *

import time

### Running SOTA baselines
This implementation is adopted from <a href="https://github.com/epfl-ml4ed/meta-transfer-learning">Swamy, et. al.</a> with slight adjustments.

In [3]:
MOOCs_list = ['villesafricaines_002.csv',
 'villesafricaines_003.csv',
 'microcontroleurs_004.csv',
 'dsp_004.csv',
 'hwts_001.csv',
 'dsp_001.csv',
 'progfun_002.csv',
 'microcontroleurs_003.csv',
 'geomatique_003.csv',
 'villesafricaines_001.csv',
 'progfun_003.csv',
 'dsp_002.csv',
 'structures_002.csv',
 'initprogcpp_001.csv',
 'analysenumerique_003.csv',
 'microcontroleurs_006.csv',
 'dsp_005.csv',
 'hwts_002.csv',
 'dsp_006.csv',
 'analysenumerique_002.csv',
 'structures_003.csv',
 'microcontroleurs_005.csv',
 'venture_001.csv',
 'analysenumerique_001.csv',
 'cpp_fr_001.csv',
 'structures_001.csv']
MOOCs_list = [i.split('.')[0] for i in MOOCs_list]

In [4]:
rnn_mode = True
data_path = '/../data'
path = os.path.join(data_path, 'extracting_concepts/')
week_type = 'eq_week'
feature_types = [ "lalle_conati", "boroujeni_et_al", "chen_cui", "marras_et_al"]
metadata = pd.read_csv(os.path.join(data_path, 'mooc', 'metadata.csv'))
early_predict = [0.4, 0.6]
epochs = 100



for MOOC in MOOCs_list:
    
    courses = [MOOC]
    course = courses[0]
    exp_type = 'baseline_' + course
    rnn_models = [bidirectional_lstm_32, 
                  bidirectional_lstm_32_32, 
                  bidirectional_lstm_64, 
                  bidirectional_lstm_32_64, 
                  bidirectional_lstm_128]
    

    save_name = 'run_history/' + course + '_baseline_model_' + week_type + '_bilstm'
    save_stats = save_name + ".csv"
    save_val_stats = save_name + '_val.csv'


    experiment_scores = pd.DataFrame(columns=['acc', 'bac','prec','rec','f1', 'auc', 'feature_type', 'week_type', 'course', 'model_name','data_balance', 'timestamp', 'percentile'])
    val_exp_scores = pd.DataFrame(columns=['acc', 'bac','prec','rec','f1', 'auc', 'feature_type', 'week_type', 'course', 'model_name','data_balance', 'timestamp', 'percentile'])

    
    counter = 0
    for percentile in early_predict:
        x_train = []
        x_test = []
        x_val = []
        y_train = []
        y_test = []
        y_val = []
        for course in courses:
            print(course, percentile)
            feature_list = []
            feature_type = "boroujeni_et_al"
            filepath = path + week_type + '-' + feature_type + '-' + course + '/feature_labels.csv'
            total_weeks = list(metadata[metadata['course_id'] == course.replace('_', '-')]['weeks'])[0]
            num_weeks = int(np.round(total_weeks * percentile))
            labels = pd.read_csv(filepath)['label-pass-fail']
            for feature_type in feature_types:
                filepath = path + week_type + '-' + feature_type + '-' + course
                #print(filepath)

                feature_current = np.load(filepath+'/feature_values.npz')['feature_values']
                feature_current = np.nan_to_num(feature_current, nan=-1)
                feature_current = feature_current[:, :num_weeks, :]
                feature_current = np.pad(feature_current, pad_width=((0, 0), (0, int(15*percentile)-feature_current.shape[1]), (0, 0)), mode='constant', constant_values=0)
                if rnn_mode:
                    feature_norm = feature_current.reshape(labels.shape[0], -1)
                    feature_norm = normalize(feature_norm)
                    feature_current = feature_norm.reshape(feature_current.shape)
                else:
                    feature_current = feature_current.reshape(labels.shape[0], -1)
                    feature_current = normalize(feature_current)

                feature_list.append(feature_current)

            course_features = np.concatenate(feature_list, axis=2)

            args_train, args_val, args_test = np.load(os.path.join(data_path, 
                                                                   'split_args', f"split_{course.replace('-', '_')}.npy"),
                                                     allow_pickle=True)
            x_train_c = course_features[args_train]
            x_val_c = course_features[args_val]
            x_test_c = course_features[args_test]
            y_train_c = labels.values[args_train]
            y_val_c = labels.values[args_val]
            y_test_c = labels.values[args_test]

            x_train.append(x_train_c)
            x_test.append(x_test_c)
            x_val.append(x_val_c)
            y_train.append(y_train_c)
            y_test.append(y_test_c)
            y_val.append(y_val_c)

            #print('course: ', course)
            #print('week_type: ', week_type)
            #print('feature_type: ', feature_types)



        x_train, x_test, x_val = np.concatenate(x_train), np.concatenate(x_test), np.concatenate(x_val)
        y_train, y_test, y_val = np.concatenate(y_train), np.concatenate(y_test), np.concatenate(y_val)


        
        
        
        best_models = []
        for model in rnn_models:
            print(model.__name__)
            current_timestamp = str(time.time())[:-2]

            # train model
            history, scores, val_scores, best_model = model(x_train, y_train, x_test, y_test, x_val, y_val, week_type, feature_types, course, percentile, current_timestamp, num_epochs=epochs)
            experiment_scores.loc[counter] = scores
            val_exp_scores.loc[counter] = val_scores
            counter += 1

            run_name = 'baseline_' + course + model.__name__  + "_ep" + str(percentile) + "_" + current_timestamp


            numpy_loss_history = np.array(history.history['loss'])
            np.savetxt('run_history/' + run_name + "_loss_history.txt", numpy_loss_history, delimiter=",")

            # save experimental scores
            experiment_scores.to_csv(save_stats)
            val_exp_scores.to_csv(save_val_stats)


            # run transfer experiments
            #transfer_experiment_scores = pd.concat([transfer_experiment_scores, predict_on_transfer(best_model, exp_type, percentile, run_name)])
            #transfer_experiment_scores.to_csv(save_name + "_transfer_results.csv")

    #experiment_scores.to_csv(save_stats)
    #val_exp_scores.to_csv(save_val_stats)
    print(experiment_scores)



villesafricaines_002 0.4
bidirectional_lstm_32


2022-09-09 12:44:49.537898: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-09-09 12:44:50.072314: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1532] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 38420 MB memory:  -> device: 0, name: NVIDIA A100-SXM4-40GB, pci bus id: 0000:c8:00.0, compute capability: 8.0


Epoch 1/100


2022-09-09 12:44:57.262254: W tensorflow/core/common_runtime/forward_type_inference.cc:231] Type inference failed. This indicates an invalid graph that escaped type checking. Error message: INVALID_ARGUMENT: expected compatible input types, but input 1:
type_id: TFT_OPTIONAL
args {
  type_id: TFT_PRODUCT
  args {
    type_id: TFT_TENSOR
    args {
      type_id: TFT_INT32
    }
  }
}
 is neither a subtype nor a supertype of the combined inputs preceding it:
type_id: TFT_OPTIONAL
args {
  type_id: TFT_PRODUCT
  args {
    type_id: TFT_TENSOR
    args {
      type_id: TFT_FLOAT
    }
  }
}

	while inferring type of node 'cond_40/output/_23'
2022-09-09 12:44:58.132202: I tensorflow/stream_executor/cuda/cuda_dnn.cc:384] Loaded cuDNN version 8100
2022-09-09 12:44:58.893434: I tensorflow/stream_executor/cuda/cuda_blas.cc:1786] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.


38/38 [==============================] - ETA: 0s - loss: 0.4858 - accuracy: 0.9104

...

1/1 [==============================] - 0s 24ms/step


/opt/conda/envs/py39/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/opt/conda/envs/py39/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


INFO:tensorflow:Assets written to: checkpoints/lstm-bi-128-1662777142.99473_final_e/assets


INFO:tensorflow:Assets written to: checkpoints/lstm-bi-128-1662777142.99473_final_e/assets


   acc       bac  prec  rec   f1       auc  \
0  0.7  0.500000   0.0  0.0  0.0  0.500000   
1  0.5  0.357143   0.0  0.0  0.0  0.357143   
2  0.7  0.500000   0.0  0.0  0.0  0.500000   
3  0.7  0.500000   0.0  0.0  0.0  0.500000   
4  0.7  0.500000   0.0  0.0  0.0  0.500000   
5  0.7  0.500000   0.0  0.0  0.0  0.500000   
6  0.7  0.500000   0.0  0.0  0.0  0.500000   
7  0.7  0.500000   0.0  0.0  0.0  0.500000   
8  0.7  0.500000   0.0  0.0  0.0  0.500000   
9  0.7  0.500000   0.0  0.0  0.0  0.500000   

                                        feature_type week_type  \
0  [lalle_conati, boroujeni_et_al, chen_cui, marr...   eq_week   
1  [lalle_conati, boroujeni_et_al, chen_cui, marr...   eq_week   
2  [lalle_conati, boroujeni_et_al, chen_cui, marr...   eq_week   
3  [lalle_conati, boroujeni_et_al, chen_cui, marr...   eq_week   
4  [lalle_conati, boroujeni_et_al, chen_cui, marr...   eq_week   
5  [lalle_conati, boroujeni_et_al, chen_cui, marr...   eq_week   
6  [lalle_conati, boroujeni_et_